In [1]:
from multi_imbalance.datasets import load_datasets
import experiment_v2 as ex
from sklearn.model_selection import StratifiedKFold
from collections import Counter, defaultdict
from multi_imbalance.utils.metrics import gmean_score
from sklearn.metrics import f1_score
from sklearn.ensemble import RandomForestClassifier
from sklearn.neighbors import KNeighborsClassifier
import numpy as np
import pandas as pd
from sklearn.tree import DecisionTreeClassifier
from utils import plot_embeddings
from sklearn.decomposition import PCA
import matplotlib.pyplot as plt
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis, QuadraticDiscriminantAnalysis

In [2]:
datasets = load_datasets()

In [3]:
ds_name = 'balance-scale'
test_on_all_folds = True
test_all_ds = True

In [4]:
datasets = ex.one_hot_encode_all(datasets)

In [5]:
from experiment import dt_name_to_cols_to_encode, dt_name_minority_classes

In [6]:
from sklearn.neighbors import KNeighborsClassifier

def calc_safety_minority_majority_5(X,y, minority_classes, metric=None):
    result_minority = {
        "safe":0,
        "borderline":0,
        "rare":0,
        "outlier":0
    }
    
    result_majority = {
        "safe":0,
        "borderline":0,
        "rare":0,
        "outlier":0
    }
    
    result = {True: result_minority, False: result_majority}
    
    
    neigh = KNeighborsClassifier(n_neighbors=5, metric=metric)
    neigh.fit(X, y)
    neighbors = neigh.kneighbors(X, 5+1, False)
    
    for i, (x, nbors) in enumerate(list(zip(X, neighbors))):
        same_class_nbrs = (y[nbors[1:]] == y[i]).sum()
        
        cond = y[i] in minority_classes
        
        if same_class_nbrs >= 4:
            result[cond]['safe'] += 1
        elif same_class_nbrs >= 2:
            result[cond]['borderline'] += 1
        elif same_class_nbrs == 1:
            result[cond]['rare'] += 1
        else:
            result[cond]['outlier'] += 1
    return result[True], result[False]

In [7]:
def standardize(X_train, X_test):
    means = X_train.mean(axis=0)
    stds = X_train.std(axis=0)
    return (X_train - means) / (stds+1e-6), (X_test - means) / (stds + 1e-6)

In [8]:
from collections import Counter
class HVDM:
    def __init__(self, X, y, categorical_cols_indices):
        self.X = X
        self.y = y
        self.stds = np.std(X, axis=0)
        self.categorical_cols_indices = categorical_cols_indices
        self.N_a_x = np.apply_along_axis(lambda x: Counter(x), 0, X)
        self.C = np.unique(y).size
        self.N_a_x_c = np.apply_along_axis(lambda x: Counter(list(zip(x, y))), 0, X)
        
    def metric(self, X1, X2):
#         print(f"X1: {X1}")
#         print(f"X2: {X2}")
        result = []
        for a in range(self.X.shape[1]):
            x = X1[a]
            y = X2[a]
            if a in self.categorical_cols_indices:
                vdm = 0
                for c in range(self.C):
                    P_a_x_c = self.N_a_x_c[a][(x,c)] / self.N_a_x[a][x]
                    P_a_y_c = self.N_a_x_c[a][(y,c)] / self.N_a_x[a][y]

                    vdm += np.abs(P_a_x_c - P_a_y_c)
                result.append(vdm)
#                     print(f"x: {x}, y: {y}, vdm: {vdm}")
            else:
                result.append(np.abs(x-y) / self.stds[a] / 4)
                
        return sum(result)
    
class HVDM:
    def __init__(self, X, y, categorical_cols_indices):
        self.X = X
        self.y = y
        self.stds = np.std(X, axis=0)
        self.categorical_cols_indices = categorical_cols_indices
        self.N_a_x = np.apply_along_axis(lambda x: Counter(x), 0, X)
        self.C = np.unique(y).size
        self.N_a_x_c = np.apply_along_axis(lambda x: Counter(list(zip(x, y))), 0, X)
        
    def metric(self, X1, X2):
#         print(f"X1: {X1}")
#         print(f"X2: {X2}")
        result = []
        for a in range(self.X.shape[1]):
            x = X1[a]
            y = X2[a]
            if a in self.categorical_cols_indices:
                try:
                    vdm = 0
                    x = round(x)
                    y = round(y)
                    for c in range(self.C):
                        P_a_x_c = self.N_a_x_c[a][(x,c)] / self.N_a_x[a][x]
                        P_a_y_c = self.N_a_x_c[a][(y,c)] / self.N_a_x[a][y]

                        vdm += np.abs(P_a_x_c - P_a_y_c)
                    result.append(vdm)
#                     print(f"x: {x}, y: {y}, vdm: {vdm}")
                except:
                    print(f"X1: {X1}")
                    print(f"X2: {X2}")
                    result.append(1)
            else:
                result.append(np.abs(x-y) / self.stds[a] / 4)
                
        return sum(result)

In [9]:
# np.apply_along_axis(lambda x: Counter(list(zip(x, y))), 0, X)

In [10]:
# np.unique(X)

In [11]:
result_dict = defaultdict(list)

safety_dict = defaultdict(list)

if test_all_ds:
    ds_names = dt_name_to_cols_to_encode.keys()
else:
    ds_names = [ds_name]
    
for dataset_name in ds_names:
# for dataset_name in list(datasets.keys()):
    print(dataset_name)
    
    safety_dict["dataset"].append(dataset_name)
    

    X, y = datasets[dataset_name]['data'], datasets[dataset_name]['target']
    X_encoded, y = datasets[f"{dataset_name}_encoded"]['data'], datasets[f"{dataset_name}_encoded"]['target']
    
    X_encoded, _ = standardize(X_encoded, X_encoded)
    
    minority_classes = dt_name_minority_classes[dataset_name]
    
    number_of_minority_examples = sum([label in minority_classes for label in y])
    
    hvdm = HVDM(X, y, dt_name_to_cols_to_encode[dataset_name])
            
    s_dict_minority, s_dict_majority = calc_safety_minority_majority_5(X, y, minority_classes, metric=hvdm.metric)
    for k,v in s_dict_minority.items():
        safety_dict[f"minority-{k}"].append(v / number_of_minority_examples)
        
    for k,v in s_dict_majority.items():
        safety_dict[f"majority-{k}"].append(v / (X_encoded.shape[0] - number_of_minority_examples))

cmc
dermatology
hayes-roth
new_vehicle
new_yeast
X1: [0.50012129 0.49993261 0.50003369 0.26118598 0.50471698 0.0075
 0.49988544 0.27619946]
X2: [0.67 0.62 0.4  0.43 0.5  0.83 0.5  0.22]
X1: [0.50012129 0.49993261 0.50003369 0.26118598 0.50471698 0.0075
 0.49988544 0.27619946]
X2: [0.44 0.38 0.48 0.32 0.5  0.83 0.53 0.22]
X1: [0.50012129 0.49993261 0.50003369 0.26118598 0.50471698 0.0075
 0.49988544 0.27619946]
X2: [0.44 0.53 0.52 0.23 0.5  0.83 0.51 0.22]
X1: [0.50012129 0.49993261 0.50003369 0.26118598 0.50471698 0.0075
 0.49988544 0.27619946]
X2: [0.69 0.6  0.51 0.13 0.5  0.83 0.52 0.22]
X1: [0.50012129 0.49993261 0.50003369 0.26118598 0.50471698 0.0075
 0.49988544 0.27619946]
X2: [0.68 0.58 0.51 0.19 0.5  0.83 0.54 0.22]
X1: [0.50012129 0.49993261 0.50003369 0.26118598 0.50471698 0.0075
 0.49988544 0.27619946]
X2: [0.42 0.5  0.53 0.22 0.5  0.83 0.5  0.22]
X1: [0.50012129 0.49993261 0.50003369 0.26118598 0.50471698 0.0075
 0.49988544 0.27619946]
X2: [0.6  0.51 0.6  0.38 0.5  0.83 0.5

X1: [0.43 0.67 0.48 0.27 0.5  0.   0.53 0.22]
X2: [0.44 0.53 0.52 0.23 0.5  0.83 0.51 0.22]
X1: [0.43 0.67 0.48 0.27 0.5  0.   0.53 0.22]
X2: [0.42 0.5  0.53 0.22 0.5  0.83 0.5  0.22]
X1: [0.43 0.67 0.48 0.27 0.5  0.   0.53 0.22]
X2: [0.67 0.62 0.4  0.43 0.5  0.83 0.5  0.22]
X1: [0.43 0.67 0.48 0.27 0.5  0.   0.53 0.22]
X2: [0.44 0.38 0.48 0.32 0.5  0.83 0.53 0.22]
X1: [0.43 0.67 0.48 0.27 0.5  0.   0.53 0.22]
X2: [0.6  0.51 0.6  0.38 0.5  0.83 0.52 0.24]
X1: [0.64 0.62 0.49 0.15 0.5  0.   0.53 0.22]
X2: [0.69 0.6  0.51 0.13 0.5  0.83 0.52 0.22]
X1: [0.64 0.62 0.49 0.15 0.5  0.   0.53 0.22]
X2: [0.4  0.4  0.43 0.19 0.5  0.83 0.48 0.22]
X1: [0.64 0.62 0.49 0.15 0.5  0.   0.53 0.22]
X2: [0.32 0.68 0.51 0.16 0.5  0.83 0.55 0.22]
X1: [0.64 0.62 0.49 0.15 0.5  0.   0.53 0.22]
X2: [0.68 0.58 0.51 0.19 0.5  0.83 0.54 0.22]
X1: [0.64 0.62 0.49 0.15 0.5  0.   0.53 0.22]
X2: [0.49 0.27 0.57 0.18 0.5  0.83 0.54 0.22]
X1: [0.64 0.62 0.49 0.15 0.5  0.   0.53 0.22]
X2: [0.57 0.52 0.46 0.2  0.5  0.83

X1: [0.43 0.39 0.54 0.21 0.5  0.   0.53 0.27]
X2: [0.57 0.52 0.46 0.2  0.5  0.83 0.52 0.41]
X1: [0.43 0.39 0.54 0.21 0.5  0.   0.53 0.27]
X2: [0.44 0.53 0.52 0.23 0.5  0.83 0.51 0.22]
X1: [0.43 0.39 0.54 0.21 0.5  0.   0.53 0.27]
X2: [0.42 0.5  0.53 0.22 0.5  0.83 0.5  0.22]
X1: [0.43 0.39 0.54 0.21 0.5  0.   0.53 0.27]
X2: [0.67 0.62 0.4  0.43 0.5  0.83 0.5  0.22]
X1: [0.43 0.39 0.54 0.21 0.5  0.   0.53 0.27]
X2: [0.44 0.38 0.48 0.32 0.5  0.83 0.53 0.22]
X1: [0.43 0.39 0.54 0.21 0.5  0.   0.53 0.27]
X2: [0.6  0.51 0.6  0.38 0.5  0.83 0.52 0.24]
X1: [0.42 0.37 0.59 0.2  0.5  0.   0.52 0.29]
X2: [0.69 0.6  0.51 0.13 0.5  0.83 0.52 0.22]
X1: [0.42 0.37 0.59 0.2  0.5  0.   0.52 0.29]
X2: [0.4  0.4  0.43 0.19 0.5  0.83 0.48 0.22]
X1: [0.42 0.37 0.59 0.2  0.5  0.   0.52 0.29]
X2: [0.32 0.68 0.51 0.16 0.5  0.83 0.55 0.22]
X1: [0.42 0.37 0.59 0.2  0.5  0.   0.52 0.29]
X2: [0.68 0.58 0.51 0.19 0.5  0.83 0.54 0.22]
X1: [0.42 0.37 0.59 0.2  0.5  0.   0.52 0.29]
X2: [0.49 0.27 0.57 0.18 0.5  0.83

X1: [0.5  0.34 0.55 0.21 0.5  0.   0.49 0.22]
X2: [0.44 0.53 0.52 0.23 0.5  0.83 0.51 0.22]
X1: [0.5  0.34 0.55 0.21 0.5  0.   0.49 0.22]
X2: [0.42 0.5  0.53 0.22 0.5  0.83 0.5  0.22]
X1: [0.5  0.34 0.55 0.21 0.5  0.   0.49 0.22]
X2: [0.67 0.62 0.4  0.43 0.5  0.83 0.5  0.22]
X1: [0.5  0.34 0.55 0.21 0.5  0.   0.49 0.22]
X2: [0.44 0.38 0.48 0.32 0.5  0.83 0.53 0.22]
X1: [0.5  0.34 0.55 0.21 0.5  0.   0.49 0.22]
X2: [0.6  0.51 0.6  0.38 0.5  0.83 0.52 0.24]
X1: [0.61 0.6  0.55 0.21 0.5  0.   0.5  0.25]
X2: [0.69 0.6  0.51 0.13 0.5  0.83 0.52 0.22]
X1: [0.61 0.6  0.55 0.21 0.5  0.   0.5  0.25]
X2: [0.4  0.4  0.43 0.19 0.5  0.83 0.48 0.22]
X1: [0.61 0.6  0.55 0.21 0.5  0.   0.5  0.25]
X2: [0.32 0.68 0.51 0.16 0.5  0.83 0.55 0.22]
X1: [0.61 0.6  0.55 0.21 0.5  0.   0.5  0.25]
X2: [0.68 0.58 0.51 0.19 0.5  0.83 0.54 0.22]
X1: [0.61 0.6  0.55 0.21 0.5  0.   0.5  0.25]
X2: [0.49 0.27 0.57 0.18 0.5  0.83 0.54 0.22]
X1: [0.61 0.6  0.55 0.21 0.5  0.   0.5  0.25]
X2: [0.57 0.52 0.46 0.2  0.5  0.83

X1: [0.59 0.45 0.53 0.19 0.5  0.   0.59 0.27]
X2: [0.6  0.51 0.6  0.38 0.5  0.83 0.52 0.24]
X1: [0.57 0.47 0.6  0.18 0.5  0.   0.51 0.22]
X2: [0.69 0.6  0.51 0.13 0.5  0.83 0.52 0.22]
X1: [0.57 0.47 0.6  0.18 0.5  0.   0.51 0.22]
X2: [0.4  0.4  0.43 0.19 0.5  0.83 0.48 0.22]
X1: [0.57 0.47 0.6  0.18 0.5  0.   0.51 0.22]
X2: [0.32 0.68 0.51 0.16 0.5  0.83 0.55 0.22]
X1: [0.57 0.47 0.6  0.18 0.5  0.   0.51 0.22]
X2: [0.68 0.58 0.51 0.19 0.5  0.83 0.54 0.22]
X1: [0.57 0.47 0.6  0.18 0.5  0.   0.51 0.22]
X2: [0.49 0.27 0.57 0.18 0.5  0.83 0.54 0.22]
X1: [0.57 0.47 0.6  0.18 0.5  0.   0.51 0.22]
X2: [0.57 0.52 0.46 0.2  0.5  0.83 0.52 0.41]
X1: [0.57 0.47 0.6  0.18 0.5  0.   0.51 0.22]
X2: [0.44 0.53 0.52 0.23 0.5  0.83 0.51 0.22]
X1: [0.57 0.47 0.6  0.18 0.5  0.   0.51 0.22]
X2: [0.42 0.5  0.53 0.22 0.5  0.83 0.5  0.22]
X1: [0.57 0.47 0.6  0.18 0.5  0.   0.51 0.22]
X2: [0.67 0.62 0.4  0.43 0.5  0.83 0.5  0.22]
X1: [0.57 0.47 0.6  0.18 0.5  0.   0.51 0.22]
X2: [0.44 0.38 0.48 0.32 0.5  0.83

...

X1: [ 58.    0.    4.  170.  225.    1.    2.  146.    1.    2.8   2.    2.
   6. ]
X2: [5.30066225e+01 7.41721854e-01 3.05298013e+00 1.29284768e+02
 2.07516556e+02 1.39072848e-01 7.94701987e-01 1.51397351e+02
 2.78145695e-01 1.03509934e+00 1.59602649e+00 5.50814570e-01
 4.77627152e+00]
X1: [ 58.    0.    4.  170.  225.    1.    2.  146.    1.    2.8   2.    2.
   6. ]
X2: [5.58618421e+01 6.18421053e-01 3.26315789e+00 1.34078947e+02
 2.85611842e+02 1.57894737e-01 1.18421053e+00 1.47828947e+02
 3.75000000e-01 1.04407895e+00 1.60526316e+00 7.85467105e-01
 4.69736842e+00]
X1: [ 58.    0.    4.  170.  225.    1.    2.  146.    1.    2.8   2.    2.
   6. ]
X2: [5.65600000e+01 7.73333333e-01 3.33333333e+00 1.28840000e+02
 2.05093333e+02 1.46666667e-01 9.86666667e-01 1.32666667e+02
 4.26666667e-01 1.51333333e+00 1.85333333e+00 7.65213333e-01
 5.16250667e+00]
X1: [ 58.    0.    4.  170.  225.    1.    2.  146.    1.    2.8   2.    2.
   6. ]
X2: [4.95000000e+01 7.10526316e-01 2.77631579e+00 1.

   7. ]
X2: [5.65600000e+01 7.73333333e-01 3.33333333e+00 1.28840000e+02
 2.05093333e+02 1.46666667e-01 9.86666667e-01 1.32666667e+02
 4.26666667e-01 1.51333333e+00 1.85333333e+00 7.65213333e-01
 5.16250667e+00]
X1: [ 67.    1.    3.  152.  212.    0.    2.  150.    0.    0.8   2.    0.
   7. ]
X2: [4.95000000e+01 7.10526316e-01 2.77631579e+00 1.29723684e+02
 2.09907895e+02 1.31578947e-01 6.05263158e-01 1.69881579e+02
 1.31578947e-01 5.63157895e-01 1.34210526e+00 3.39236842e-01
 4.39511842e+00]
X1: [ 67.    1.    3.  152.  212.    0.    2.  150.    0.    0.8   2.    0.
   7. ]
X2: [5.49729730e+01 7.83783784e-01 3.67567568e+00 1.28162162e+02
 1.84810811e+02 1.35135135e-01 9.18918919e-01 1.30378378e+02
 4.86486486e-01 1.64864865e+00 1.91891892e+00 6.48648649e-01
 5.21621622e+00]
X1: [ 67.    1.    3.  152.  212.    0.    2.  150.    0.    0.8   2.    0.
   7. ]
X2: [5.81052632e+01 7.63157895e-01 3.00000000e+00 1.29500000e+02
 2.24842105e+02 1.57894737e-01 1.05263158e+00 1.34894737e+02
 3

X1: [ 41.   1.   2. 120. 157.   0.   0. 182.   0.   0.   1.   0.   3.]
X2: [5.65600000e+01 7.73333333e-01 3.33333333e+00 1.28840000e+02
 2.05093333e+02 1.46666667e-01 9.86666667e-01 1.32666667e+02
 4.26666667e-01 1.51333333e+00 1.85333333e+00 7.65213333e-01
 5.16250667e+00]
X1: [ 41.   1.   2. 120. 157.   0.   0. 182.   0.   0.   1.   0.   3.]
X2: [4.95000000e+01 7.10526316e-01 2.77631579e+00 1.29723684e+02
 2.09907895e+02 1.31578947e-01 6.05263158e-01 1.69881579e+02
 1.31578947e-01 5.63157895e-01 1.34210526e+00 3.39236842e-01
 4.39511842e+00]
X1: [ 41.   1.   2. 120. 157.   0.   0. 182.   0.   0.   1.   0.   3.]
X2: [5.49729730e+01 7.83783784e-01 3.67567568e+00 1.28162162e+02
 1.84810811e+02 1.35135135e-01 9.18918919e-01 1.30378378e+02
 4.86486486e-01 1.64864865e+00 1.91891892e+00 6.48648649e-01
 5.21621622e+00]
X1: [ 41.   1.   2. 120. 157.   0.   0. 182.   0.   0.   1.   0.   3.]
X2: [5.81052632e+01 7.63157895e-01 3.00000000e+00 1.29500000e+02
 2.24842105e+02 1.57894737e-01 1.052631

   7. ]
X2: [4.77894737e+01 6.57894737e-01 2.71052632e+00 1.28078947e+02
 1.92210526e+02 1.57894737e-01 5.26315789e-01 1.70789474e+02
 1.31578947e-01 3.89473684e-01 1.21052632e+00 3.52394737e-01
 4.31655263e+00]
X1: [ 68.    1.    4.  144.  193.    1.    0.  141.    0.    3.4   2.    2.
   7. ]
X2: [5.12105263e+01 7.63157895e-01 2.84210526e+00 1.31368421e+02
 2.27605263e+02 1.05263158e-01 6.84210526e-01 1.68973684e+02
 1.31578947e-01 7.36842105e-01 1.47368421e+00 3.26078947e-01
 4.47368421e+00]
X1: [ 68.    1.    4.  144.  193.    1.    0.  141.    0.    3.4   2.    2.
   7. ]
X2: [5.50394737e+01 6.84210526e-01 3.25000000e+00 1.31394737e+02
 2.57447368e+02 1.44736842e-01 1.18421053e+00 1.47486842e+02
 3.68421053e-01 9.36842105e-01 1.63157895e+00 6.36723684e-01
 4.64473684e+00]
X1: [ 68.    1.    4.  144.  193.    1.    0.  141.    0.    3.4   2.    2.
   7. ]
X2: [5.66842105e+01 5.52631579e-01 3.27631579e+00 1.36763158e+02
 3.13776316e+02 1.71052632e-01 1.18421053e+00 1.48171053e+02
 3

new_ecoli
new_led7digit
new_winequality-red
thyroid-newthyroid


In [12]:
safety_df = pd.DataFrame.from_dict(safety_dict)

In [13]:
safety_df[sorted(safety_df.filter(regex=("dataset|minority")).columns)].style.highlight_max(color = 'lightgreen', axis = 1)

In [14]:
safety_df[sorted(safety_df.filter(regex=("dataset|majority")).columns)].style.highlight_max(color = 'lightgreen', axis = 1)